In [ ]:
import Metashape
from pathlib import Path
import geopandas as gpd
import pandas as pd
import numpy as np
from shapely.geometry import Point
from sklearn.metrics import r2_score, mean_squared_error
from scipy.interpolate import griddata
import rasterio
import rioxarray as rxr
import xarray as xr

# Key files to import:
KW_dem = rasterio.open(Path(r"..\export\dem\KW_dem_10-255.tif"))
dem = rxr.open_rasterio(Path(r"..\export\dem\KW_dem_10-255.tif"), masked=True)
metashape_path = Path(r"..\metashape\Konusdalen_West.psx")
npidem = rxr.open_rasterio(Path(r"..\NPI\S0_DTM5_2009_13835_33.tif"), masked=False) # Download from https://data.npolar.no/dataset/dce53a47-c726-4845-85c3-a65b46fe2fea

In [ ]:
def calculate_dem_values(gdf, dem):
    gdf["DEM (m)"] = [val[0] for val in dem.sample(list(zip(gdf['geometry'].x, gdf['geometry'].y)))]
    gdf["Alt.-DEM (m)"] = gdf["Altitude (m)"]-gdf["DEM (m)"]
    return gdf
    
def r2_rmse( g ): # from https://stackoverflow.com/questions/47914428/python-dataframe-calculating-r2-and-rmse-using-groupby-on-one-column
    r2 = r2_score( g['Actual'], g['Predicted'] )
    rmse = np.sqrt( mean_squared_error( g['Actual'], g['Predicted'] ) )
    return pd.Series( dict(  r2 = r2, rmse = rmse ) )

def cal_RMS(x):
    return np.sqrt(sum(x**2/len(x)))
    
def create_gcp_output(gdf):
    out = gdf.copy()
    out["Marker"] = out["Marker"].apply(lambda x: str(x).zfill(2))
    out.loc[out["enabled"]==True,"Type"] = "GCP"
    out.loc[out["enabled"]==False,"Type"] = "CP" 
    out["Northing (y, m)"] = out.geometry.y
    out["Easting (x, m)"] = out.geometry.x
    mean = out.groupby("Type").agg("mean").reset_index(drop=False)
    mean.loc[:,["Marker","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    
    mean_excl = out.drop(9).groupby("Type").agg("mean").reset_index(drop=False)
    mean_excl = mean_excl.drop(0)
    mean_excl.loc[:,["Marker","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    mean.loc[:,"Marker"] = "Mean"
    mean_excl.loc[:,"Marker"] = "Mean (excl. GCP 02)"
    rms =  out.groupby("Type").agg(cal_RMS).reset_index(drop=False)
    rms.loc[:,["Marker","Images","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    rms.loc[:,"Marker"] = "RMSE"
    rms_excl =  out.drop(9).groupby("Type").agg(cal_RMS).reset_index(drop=False)
    rms_excl = rms_excl.drop(0)
    rms_excl.loc[:,["Marker","Images","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    rms_excl.loc[:,"Marker"] = "RMSE (excl. GCP 02)"
    out = out.append(mean, ignore_index=True)
    out = out.append(mean_excl, ignore_index=True)
    out = out.append(rms, ignore_index=True)
    out = out.append(rms_excl, ignore_index=True)
    
    table = out[["Marker",
               "Type",
               "Images",
               "Northing (y, m)",
               "Easting (x, m)",
               "Altitude (m)", 
               "Error (x, m)", 
               "Error (y, m)", 
               "Error (z, m)", 
               "Error (xyz, m)",
               "DEM (m)",
               "Alt.-DEM (m)"
              ]]
    table["Marker"].astype(str)
    table = table.round(3)
    print(table[table["Type"]=="GCP"].sort_values(by="Marker").fillna("-").to_markdown(index=False, floatfmt=[".0f",".0f",".0f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f"]))
    print(table[table["Type"]=="CP"].sort_values(by="Marker").fillna("-").to_markdown(index=False, floatfmt=(".0f",".0f",".0f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f")))
    return out

def create_dgnss_output(dgnss):
    out = dgnss.copy()
    out["Northing (y, m)"] = out.geometry.y
    out["Easting (x, m)"] = out.geometry.x
    mean = out.groupby("Point_Role").agg("mean").reset_index(drop=False)
    mean.loc[:,["Point_ID","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    mean.loc[:,"Point_ID"] = "Mean"

    rms =  out.groupby("Point_Role").agg(cal_RMS).reset_index(drop=False)
    rms.loc[:,["Point_ID","Images","Northing (y, m)","Easting (x, m)","Altitude (m)","DEM (m)"]] = np.nan
    rms.loc[:,"Point_ID"] = "RMSE"
    out = out.append(mean, ignore_index=True)
    out = out.append(rms, ignore_index=True)
    
    table = out[["Point_ID",
                 "Point_Role",
                 "Annot_1",
                 "Annot_2",
                 "Northing (y, m)",
               "Easting (x, m)",
               "Altitude (m)",
               "DEM (m)",
               "Alt.-DEM (m)"
              ]]
    table = table.round(3)
    print(table[table["Point_Role"]=="Code PP"].sort_values(by="Point_ID").fillna("-").to_markdown(index=False, floatfmt=[".0f",".0f",".0f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f"]))
    print(table[table["Point_Role"]=="Widelane PP"].sort_values(by="Point_ID").fillna("-").to_markdown(index=False, floatfmt=(".0f",".0f",".0f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f")))
    print(table[table["Point_Role"]=="Fixed PP"].sort_values(by="Point_ID").fillna("-").to_markdown(index=False, floatfmt=(".0f",".0f",".0f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f",".3f")))
    return out   


# Getting GCP data from the metashape project

In [ ]:
doc = Metashape.Document()
doc.open(str(metashape_path))

### Calculating the GCP positions
chunk = doc.chunk
chunk.crs = Metashape.CoordinateSystem("EPSG::32633")
df = pd.DataFrame()
for marker in chunk.markers:
    try:
        dct = {
             "Marker": int(marker.label),
             "Images": len(marker.projections.items()),
             "enabled": marker.reference.enabled,
             "Accuracy (xyz, m)": marker.reference.accuracy[0],
             "lon": marker.reference.location[0],
             "lat": marker.reference.location[1],
             "Altitude (m)": marker.reference.location[2]
        }
        try:
            error = chunk.transform.matrix.mulp(marker.position) - chunk.crs.unproject(marker.reference.location)
            m = chunk.crs.localframe(chunk.transform.matrix.mulp(marker.position))
            error = m.mulv(error)
            dct.update(
                {"Error (x, m)": error.x,
                 "Error (y, m)": error.y,
                 "Error (z, m)": error.z,
                 "Error (xyz, m)": error.norm()}
            )
        except:
            dct.update(
                {"Error (x, m)": np.nan,
                 "Error (y, m)": np.nan,
                 "Error (z, m)": np.nan,
                 "Error (xyz, m)": np.nan}
            )
        dct = {k:[v] for k,v in dct.items()}
        df = df.append(pd.DataFrame(dct),ignore_index=True)
        #print(temp_dict)#.label, error.norm(), error.x, error.y, error.z)
    except:
        pass
gdf = gpd.GeoDataFrame(df, geometry = [Point(xy) for xy in zip(df.lon,df.lat)])
gdf.crs = "epsg:32633"
#gdf = gdf.to_crs("epsg:32633")

# Calculating errors

In [ ]:
gdf = calculate_dem_values(gdf)
out = create_gcp_output(gdf)#.drop(9))
#gdf.to_file("data/gcp.gpkg",driver="GPKG")

In [ ]:
out = create_gcp_output(gdf.drop(9)) # Removing outlier

## Other dGNSS measurements

In [ ]:
dgnss = gpd.read_file(r"..\data\dGPS\Deltaneset_2021\Point\0.shp")
dgnss["Northing (y, m)"] = dgnss.geometry.x
dgnss["Easting (x, m)"] = dgnss.geometry.y
dgnss["Altitude (m)"] = dgnss["geometry"].apply(lambda geom: geom.coords[0][2])
dgnss = calculate_dem_values(dgnss, KW_dem)
dgnss_out = create_dgnss_output(dgnss)#.drop(9))
dgnss_out.to_file("data/dgnss_out.gpkg",driver="GPKG")

# NPI DEM

In [ ]:
npidem = npidem.rio.reproject(dst_crs="EPSG:32633")
npidem = npidem.where(npidem != npidem.data[0][0][0])

Match the projections of the two DEMs - using NPI grid resolution

In [ ]:
diff_dem = npidem-dem.rio.reproject_match(npidem).assign_coords({
    "x": npidem.x,
    "y": npidem.y,
})

In [ ]:
import numpy as np
np.min(diff_dem.data[0][~np.isnan(diff_dem.data[0])])